# Fait du poireautage¹ de données comme un pro



----

1: Traduction approximative

![leek](https://media.giphy.com/media/d8KkDupA6b3o9UQlbv/source.gif)

In [1]:
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.datasets import make_classification
from sklearn.model_selection import cross_val_score, StratifiedShuffleSplit
from sklearn.metrics import cohen_kappa_score, make_scorer
from tqdm.auto import tqdm

In [2]:
n_samples = 100
n_features = 3072
n_classes = 5
n_features_selection = 927

In [3]:
X, y = make_classification(n_samples, n_features, 
                           n_classes=n_classes,
                           n_informative=10,
                           n_redundant=0,
                           n_repeated=0,
                           class_sep=3,
                           flip_y=0.01)

In [4]:
X.shape, 

((100, 3072),)

In [5]:
y.shape

(100,)

In [6]:
kf = StratifiedShuffleSplit(n_splits=2)

![Stratified Shuffle](https://scikit-learn.org/stable/_images/sphx_glr_plot_cv_indices_0091.png)

In [7]:
def benchmark(X):
    s = []
    for i in tqdm(range(25)):
        s += [cross_val_score(RandomForestClassifier(), X, y, cv=kf, n_jobs=-1, scoring=make_scorer(cohen_kappa_score))]
    s = np.array(s)
    print('𝛋 = {:.2f} ± {:.2f}'.format(s.mean(), s.std()))

benchmark(X)


𝛋 = 0.19 ± 0.19


In [8]:
def select_best_features(X):
    clf = RandomForestClassifier(random_state=0)
    clf.fit(X, y)

    ibest = np.argsort(clf.feature_importances_)[-n_features_selection:]

    return X[:,ibest]

In [9]:
select_best_features(X).shape

(100, 927)

In [10]:
benchmark(select_best_features(X))


𝛋 = 0.52 ± 0.19


# Who cares about data quality anyway

now same but full random X

In [11]:
Xr = np.random.random((n_samples, n_features))

In [12]:
Xr.shape

(100, 3072)

In [13]:
benchmark(Xr)


𝛋 = 0.05 ± 0.14


In [14]:
benchmark(select_best_features(Xr))


𝛋 = 0.18 ± 0.17


![](https://media1.tenor.com/images/766adcaf4097f8c68aa069ad0fbaeb79/tenor.gif)

- <https://www.nature.com/articles/s41598-019-56185-5>
- <https://static-content.springer.com/esm/art%3A10.1038%2Fs41598-019-56185-5/MediaObjects/41598_2019_56185_MOESM1_ESM.pdf>
- Part 7.10.2 (p. 264) of <https://web.stanford.edu/~hastie/ElemStatLearn/>
- <https://towardsdatascience.com/data-leakage-in-machine-learning-10bdd3eec742>
- <https://www.reddit.com/r/MachineLearning/comments/jviymn/d_i_keep_running_across_studies_designed_this_way/>

## RESPECTEZ LES GESTES BARRIÈRES

1. **If train/val then test is your god**
2. Feature selection should be done in CV
3. _For nihilists_: get more training data.
4. _Get better data._